In [393]:
import geopandas as gpd
import pandas as pd
import osmnx as ox
import matplotlib.pyplot as plt
import folium
import alphashape
import numpy as np
from tqdm.notebook import tqdm
import networkx as nx
%matplotlib inline

In [423]:
class Network:
    def __init__(self, crs = 32618):
        self.crs = crs
        self.n_pot = None
        self.n_pot_nodes = None
        self.n_pot_edges = None
        self.n_ex = None
        self.n_ex_nodes = None
        self.n_ex_edges = None
        self.trips = None
        self.map_pot = None
        self.map_ex = None
        self.map_routes = None
        self.trips = None
        self.trips_within = None
        self.sample = None
        self.boundaries = None
        self.routes = []
        self.routes_summary = None
        
    def load_n_pot(self,path):
        self.n_pot = ox.io.load_graphml(path)
        self.n_pot = ox.project_graph(self.n_pot)
        # self.n_pot = ox.consolidate_intersections(G_proj, rebuild_graph=True, tolerance=10, dead_ends=False)
        self.n_pot_nodes,self.n_pot_edges = ox.graph_to_gdfs(self.n_pot)
        
    def filter_n_pot(self):
        self.n_pot_edges[self.n_pot_eges.highway.isin(['residential','primary','secondary','tertiary','tertiary_link'])]
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)

    def plot_n_pot(self, nodes = False):
        if self.n_pot == None:
            print('No potential network loaded')
        else:
            self.map_pot = self.n_pot_edges.explore(color = 'black')
            if nodes:
                self.n_pot_nodes.explore(m = self.map_pot)
            display(self.map_pot)

    def load_n_ex(self,path):
        self.n_ex = ox.io.load_graphml(path)
        self.n_ex = ox.project_graph(self.n_ex)
        # self.n_ex = ox.consolidate_intersections(G_proj, rebuild_graph=True, tolerance=10, dead_ends=False)
        self.n_ex_nodes,self.n_ex_edges = ox.graph_to_gdfs(self.n_ex)

    def filter_n_ex(self,highway_type = 'cycleway'):
        self.n_ex_edges = self.n_ex_edges[self.n_ex_edges.highway == highway_type]
        self.n_ex = ox.graph_from_gdfs(self.n_ex_nodes,self.n_ex_edges)

    def plot_n_ex(self, nodes = False):
        if self.n_ex == None:
            print('No existing network loaded')
        else:
            self.map_ex = self.n_ex_edges.explore(color = 'black')
            if nodes:
                self.n_ex_nodes.explore(m = self.map_ex)
            display(self.map_ex)

    def load_trips(self, path, cols = ['ipere','feuillet','rang','xorig','yorig','xdest','ydest','mode','potVelo']):
        self.trips = pd.read_csv(path)
        self.trips = self.trips[self.trips.potVelo == 1]
        self.trips = self.trips[cols]
        self.trips = gpd.GeoDataFrame(self.trips, geometry=gpd.points_from_xy(self.trips.xorig, self.trips.yorig), crs=32188)
        self.trips = self.trips.rename(columns = {'geometry': 'orig'})
        self.trips = self.trips.assign(dest = gpd.points_from_xy(self.trips.xdest, self.trips.ydest,crs=32188))
        self.trips = self.trips.set_geometry('orig')
        self.trips = self.trips.to_crs(self.crs)
        self.boundaries = gpd.GeoDataFrame({'name':['region']},geometry = gpd.GeoSeries(self.n_pot_nodes.geometry.union_all()).concave_hull(0.3)
                                           , crs = self.crs)
        
        self.trips = self.trips.to_crs(self.crs)
        self.trips_within = gpd.sjoin(self.trips, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]
        self.trips_within = self.trips_within.set_geometry('dest')
        self.trips_within = self.trips_within.to_crs(self.crs)
        self.trips_within = gpd.sjoin(self.trips_within, self.boundaries, how='inner', predicate='within')[list(self.trips.columns)]

    def compute_routes(self, network, sample_size = None, spec_route = None, weight = 'gencost'):
        if sample_size is None:
            sample_size = len(self.trips_within)
            self.sample = self.trips_within.sample(sample_size)
        else:
            self.sample = pd.concat([self.sample,self.trips_within.sample(sample_size)])

        if spec_route is not None:
            self.sample = self.trips_within[self.trips_within.ipere == spec_route]
        network = ox.projection.project_graph(network, to_crs = self.crs)
        o_nodes,o_dists = ox.nearest_nodes(network,self.sample.orig.x.values,self.sample.orig.y.values, return_dist=True)
        d_nodes,d_dists = ox.nearest_nodes(network,self.sample.dest.x.values,self.sample.dest.y.values, return_dist=True)
        routes = ox.shortest_path(network, o_nodes, d_nodes, weight=weight)
        self.routes+=routes

    def plot_routes(self,network):
        routes_edges = []
        unsolved = []
        static = []
        
        for i in tqdm(range(len(self.routes))):
            if self.routes[i] is not None:
                if len(self.routes[i])>1:
                    edges = ox.routing.route_to_gdf(network,self.routes[i])
                    edges = edges.assign(route_number = i)
                    routes_edges.append(edges)
            elif self.routes[i] is None:
                unsolved.append(i)
            else:
                static.append(self.routes[i])
        
        all_routes_edges = pd.concat(routes_edges)
        self.routes_summary = all_routes_edges[['length','gencost','route_number']].groupby(['route_number']).sum()

        self.sample = self.sample.set_geometry('orig')
        self.map_routes = self.sample.explore(color='blue', name='orig')
        self.sample = self.sample.set_geometry('dest')
        map2 = self.sample.explore(color='red', name='dest', m=self.map_routes)
        map3 = self.boundaries.explore(m = self.map_routes, name = 'boundaries', fill = False)
        map4 = self.n_ex_edges.explore(color='black', name='existing', m=self.map_routes)
        map5 = self.n_pot_edges.explore(color='black', name='potential', m=self.map_routes)
        map8 = all_routes_edges.explore(color = 'yellow', name = 'routes', m = self.map_routes)
        folium.LayerControl().add_to(self.map_routes)
        display(self.map_routes)

    def weight_network(self,cycleway_ben_factor=0.9):
        self.n_pot_edges['gencost'] = self.n_pot_edges["length"] * self.n_pot_edges["highway"].apply(lambda x: cycleway_ben_factor if x == "cycleway" else 1)
        self.n_pot = ox.graph_from_gdfs(self.n_pot_nodes,self.n_pot_edges)

In [424]:
n = Network()
ex = 'Data/Reseaux/EX_Villeray-Saint-Michel-Parc-Extension.graphml'
pot = 'Data/Reseaux/POT_Villeray-Saint-Michel-Parc-Extension.graphml'
trips = 'Data/od18_extraqit_20250123/od18_extraqit_20250123.csv'

In [425]:
n.load_n_pot(pot)
n.load_n_ex(ex)
n.load_trips(trips)

In [426]:
n.weight_network(cycleway_ben_factor=0.1)

In [427]:
n.routes = []
n.sample = None
n.compute_routes(n.n_pot, sample_size = 1,spec_route = 38859 ,weight='gencost')

In [428]:
n.plot_routes(n.n_pot)

  0%|          | 0/1 [00:00<?, ?it/s]